In [61]:
import os
gpu_num = 0
os.environ["CUDA_VISIBLE_DEVICES"] = f"{gpu_num}"
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
#os.environ['DRJIT_LIBLLVM_PATH'] = '/home/usare/.conda/envs/sionnasim/lib/libLLVM-17.so'

In [62]:
import pandas as pd
import numpy as np
import tensorflow as tf
    
from sionna.rt import load_scene, Transmitter, Receiver, PlanarArray, Camera
from sionna.channel import subcarrier_frequencies, cir_to_ofdm_channel
import matplotlib.pyplot as plt

In [63]:
scene = load_scene("./scenes/scene1.xml")

In [64]:
scene.tx_array = PlanarArray(
                                num_rows=4,
                                num_cols=4,
                                vertical_spacing=0.5,
                                horizontal_spacing=0.5,
                                pattern="tr38901",
                                polarization="V"
                            )
scene.rx_array = PlanarArray(
                                num_rows=1,
                                num_cols=1,
                                vertical_spacing=0.5,
                                horizontal_spacing=0.5,
                                pattern="iso",
                                polarization="V"
                            )
tx = Transmitter("tx", [-262, 192, 65], [0.0, 0.0, 0.0])
scene.add(tx)

In [65]:
from scipy.interpolate import interp1d
import ast
# Read the Excel file
df = pd.read_excel('output.xlsx')

# Extract the desired columns
desired_columns = ['vehid','steps', 'coord']
df = df[desired_columns]

In [66]:
#Pega os ids dos veiculos
unique_vehids = df['vehid'].unique()
#Pega o maior e o menor valor da coluna steps para saber qual a duração da simulação
max_steps = df['steps'].max()
min_steps = df['steps'].min()
simulation_duration = max_steps - min_steps + 1

# Array que receberá os objetos com as informações dos veiculos
vehicles = []

# Calculando o valores de passos necessarios para ter uma resolução de 1ms, pois o SUMO simula com passo a cada 1s
interpolate_steps = int(1/1e-3)
# 1000 pontos entre cada par de coordenadas

#Loop percorrendo cada veiculo para montar o objeto com as informacoes
for vehid in unique_vehids:
    coords=[]
    vehid_df = df[df['vehid'] == vehid]
    #Acha o primeiro Step em que o carro é rendezirado
    first_apper = vehid_df['steps'].iloc[0]
    #Acha o ultimo Step em que o carro é rendezirado
    last_apper = vehid_df['steps'].iloc[-1]
    #Pega a lista de coordenadas do veiculo
    coords_list = vehid_df['coord'].tolist()

    #Transforma a lista de strings em uma lista de tuplas
    coords = [ast.literal_eval(elem) for elem in coords_list]
    x, y = zip(*coords)
    x = np.array(x)
    y = np.array(y)

    # Cria uma função de interpolação linear para
    f = interp1d(x, y)
    
    # Generate new x values: since we want 4000 new points between each pair, calculate the new step
    new_x = np.linspace(x.min(), x.max(), num=len(x) + interpolate_steps * (len(x) - 1))

    # Use the interpolation function to generate new y values
    new_y = f(new_x)
    obj = {
        'vehid': vehid,
        'first_apper': first_apper,
        'last_apper':last_apper,
        'coords': list(zip(new_x, new_y)),
    }
    vehicles.append(obj)

In [67]:
#####################
# For test purposes #
#####################

# Esses parametros foram calculados para visualizar a cena no render do sionna
x_cam = -50
y_cam = -50
z_cam = 200
cam = Camera(name="cam",position=[x_cam,y_cam,z_cam])

#Direcionando a camera para o melhor enquadramento
cam.look_at([0,0,0])
scene.add(Camera("cam", position=[-500,240,45], look_at=[0,50,0], ))

medium_resolution = [560,420]


#####################
# For test purposes #
#####################

In [68]:

# Esse intervalo de tempo foi definido de acordo com que todos os veiculo apareçam na cena simultaneamente
first_step = 23*interpolate_steps +100
last_step = first_step + 1000#36*interpolate_steps
loop_step = 1
for interpol_step in range(first_step,last_step,1000):
    for i,veh in enumerate(vehicles[0:1]):
            #Pega as coordenadas do veiculo
            current_position_index = interpol_step-(veh['first_apper']-min_steps)*interpolate_steps
            x1,y1 = veh['coords'][current_position_index]
            x1 = x1
            y1 = y1
            print(x1,y1)
            print(scene.size)
            #Adiciona o veiculo na cena caso seja o seu primeiro step
            if interpol_step == first_step:
                scene.add(Receiver(name=veh["vehid"], position=[x1,y1,1.5]))
            else:
                scene.receivers[veh["vehid"]].position = [x1,y1,1.5]
    #Computa os caminhos de propagação
    paths = scene.compute_paths(diffraction=True) 
    #Renderiza a cena
    # scene.render_to_file(filename=f"renders/render_{interpol_step}.png",
    #                      resolution=medium_resolution,
    #                      camera="cam",
    #                      paths=paths, 
    #                      fov=82)

22.053907880562743 180.79767842399463
tf.Tensor([499.2387  499.23877  81.8    ], shape=(3,), dtype=float32)


In [69]:
scene.preview()

Renderer(camera=PerspectiveCamera(aspect=1.31, children=(DirectionalLight(intensity=0.25, position=(0.0, 0.0, …